In [1]:
import time
import re 
import datetime
import asyncio
from dataclasses import dataclass
from multiprocessing import Pool

from multiprocess import Pool as mPool
import aiohttp
from tqdm import tqdm
from bs4 import BeautifulSoup
from selenium import webdriver
import pandas as pd
import nest_asyncio
nest_asyncio.apply()

DEPTH = 350

chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument("--blink-settings=imagesEnabled=false")
# chrome_options.add_argument("headless")
chrome_options.add_argument("no-sandbox")
chrome_options.add_argument("disable-dev-shm-usage")

In [2]:
@dataclass
class Article:
    topic: str = None
    url: str = None
    title: str = None
    content: str = None
    datetime: str = None

In [3]:
driver = webdriver.Chrome(options=chrome_options)

In [3]:
def get_pages():
    
    # scroll page to automatically load more articles
    last_count = 0
    scroll_attempts = 0
    max_no_new_data_attempts = 3

    for _ in tqdm(range(DEPTH), leave=False):
        html = driver.page_source
        soup = BeautifulSoup(html, features="lxml")
        articles = soup.find_all('a', {'class': 'search-item__link js-search-item-link'})
        current_count = len(articles)

        if current_count > last_count:
            # Количество статей увеличилось
            print(f"Статей: {last_count} → {current_count} (+{current_count - last_count})")
            last_count = current_count
            scroll_attempts = 0
        else:
            # Количество статей не изменилось
            scroll_attempts += 1
            print(f"Количество статей не изменилось: {current_count}. Попытка {scroll_attempts}/{max_no_new_data_attempts}")
            
            if scroll_attempts >= max_no_new_data_attempts:
                print("Загрузка новых данных остановилась, завершаем скроллинг")
                break

        driver.execute_script(
            f"window.scrollTo(0, document.body.scrollHeight - 1200)"
        )
        time.sleep(0.5)

    # Получаем финальный список ссылок
    html = driver.page_source
    soup = BeautifulSoup(html, features="lxml")
    articles = soup.find_all('a', {'class': 'search-item__link js-search-item-link'})
    a_links = [a['href'] for a in articles]
    return a_links

In [4]:
rbc_topics = {
    'Общество/Россия': 'society',
    'Экономика': 'economics',
    # 'Силовые структуры': 'politics',
    'Бывший СССР': '', 
    'Спорт': 'sport',
    'Строительство': '',
    'Туризм/Путешествия': '',
    # 'Наука и техника': 'technology_and_media',
}

rbc_url = 'https://www.rbc.ru/search/?project=rbcnews&dateFrom=01.01.2023&dateTo=31.12.2024&category={}' 
# тут менял год dateTo, чтобы выгрузить дополнительно статей, т.к есть ограничение в 2000 шт


not_found_topics =     {'Туризм/Путешествия': ['https://www.rbc.ru/tags/?&dateFrom=01.01.2023&dateTo=31.12.2025&tag=туризм',
                                               'https://www.rbc.ru/tags/?&dateFrom=01.01.2023&dateTo=31.12.2025&tag=путешествия'],
                        'Бывший СССР':         'https://www.rbc.ru/tags/?&dateFrom=01.01.2023&dateTo=31.12.2025&tag=СССР',
                        'Строительство':       'https://www.rbc.ru/search/?query=&project=realty&dateFrom=01.01.2023&dateTo=31.12.2025',
                        }

topic_urls = {}
for topic in rbc_topics:
    if rbc_topics[topic]:
        topic_urls[topic] = rbc_url.format(rbc_topics[topic]) 
    else:
        topic_urls[topic] = not_found_topics[topic]
    


In [6]:
# needed_topics = topic_urls.keys()
needed_topics = ['Общество/Россия', 'Экономика']

needed_topic_urls = {topic: topic_urls[topic] for topic in needed_topics}

In [ ]:
art_dct = {}
for topic, urls in tqdm(needed_topic_urls.items(), leave=False):
  art_tmp = []
  print(topic)

  if isinstance(urls, list):
    for url in tqdm(urls):
      driver.get(url)
      arts = get_pages()
      art_tmp.extend(arts)

  else:
    driver.get(urls)
    arts = get_pages()
    art_tmp.extend(arts)

  art_dct[topic] = art_tmp

In [ ]:
art_dct = {key: list(set(art_dct[key])) for key in art_dct}
pd.Series({key: len(set(value)) for key, value in art_dct.items()}, name='count')

In [6]:
async def fetch(session, url):
    try:
        async with session.get(url, timeout=3) as response:
            return url, await response.text()
    except TimeoutError:
        return '', ''
    

async def fetch_all(urls):
    headers = {
        'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/143.0.0.0 Safari/537.36',
        'sec-ch-ua': '"Google Chrome";v="143", "Chromium";v="143", "Not A(Brand";v="24"',
        }
    async with aiohttp.ClientSession(headers=headers) as session:
        results = await asyncio.gather(*[fetch(session, url) for url in urls])
        return results
    

def parse_article(url, html):

    soup = BeautifulSoup(html, features='lxml')
    try:
        art_content = soup.find('div', {'class': 'l-col-center-590 article__content'})
        title = art_content.find('h1', {'class': lambda x: re.match(r'article__header__title.*', x)}).text.strip()

        main_content = art_content.find('div', {'class': 'article__text article__text_free'})
        text = main_content.find_all('p')
        text = ' '.join([p.text.strip() for p in text if p.text.strip()])

        date = art_content.find('time', {'class': 'article__header__date'})
        date = datetime.datetime.fromisoformat(date['datetime'])

        article = Article(topic=None, url=url, title=title, content=text, datetime=date)

        return article
    
    except AttributeError:
        return Article()

In [7]:
def parallel_parsing_articles(responses_data):
    with Pool() as pool:
        articles = pool.starmap(parse_article, responses_data)
    return articles

def parallel_parsing_articles2(responses_data):
    with mPool() as pool:
        articles = pool.starmap(parse_article, responses_data)
    return articles

In [17]:
import pickle

# with open('arts.pkl', 'wb') as f:
# 	pickle.dump(art_dct, f)


with open('arts.pkl', 'rb') as f:
	art_dct = pickle.load(f)

In [20]:
articles = {topic: [] for topic in art_dct}

chunk_size = 20
max_articles = 100

for topic in tqdm(list(art_dct)):
    for i in tqdm(range(0, len(art_dct[topic]), chunk_size)):
        results = asyncio.run(fetch_all(art_dct[topic][i:i+chunk_size]))
        articles[topic].extend(parallel_parsing_articles2(results))
        time.sleep(10)

100%|██████████| 2/2 [40:14<00:00, 1207.34s/it]


In [21]:
articles


{'Общество/Россия': [Article(topic=None, url='https://www.rbc.ru/rbcfreenews/67468ac09a7947f172a9bb42', title='На Благовещенск обрушилась снежная «буря столетия»', content='Благовещенск в Амурской области накрыла снежная «буря столетия», осадки не прекращаются с понедельника, 25 ноября, сообщает пресс-служба администрации города в телеграм-канале. «Стихия ударила по Благовещенску: такого снегопада в областном центре не было век»,\xa0— говорится в сообщении. Снегопад получил название «буря столетия». За ночь в областном центре выпало 1,3 см осадков. Всего\xa0же с начала снегопада\xa0— 3,6 см. В результате непогоды несколько автобусов не смогли выйти в рейсы. На данный момент на маршрутах находятся от двух до шести автобусов. По данным Минтранса региона, из-за снегопада четыре утренних рейса в городе ушли на запасной аэродром в Хабаровск\xa0— из Новосибирска, Екатеринбурга, Владивостока и Москвы. На вылет из Благовещенска задерживаются все рейсы, ушедшие в Хабаровск, а также международны

In [22]:
[(a, len(articles[a])) for a in articles]

[('Общество/Россия', 2000), ('Экономика', 2000)]

In [23]:
articles_dict = {topic: [art.__dict__ for art in articles[topic]] for topic in articles}

In [24]:
articles_dict_clean = {topic: [art for art in articles_dict[topic] if art['url'] is not None] for topic in articles_dict}

In [25]:
[(a, len(articles_dict_clean[a])) for a in articles_dict_clean]

[('Общество/Россия', 1672), ('Экономика', 1643)]

In [26]:
res_art_lst = []
for topic in articles_dict_clean:
    tmp_df = pd.DataFrame(articles_dict_clean[topic])
    tmp_df['topic'] = topic
    res_art_lst.append(tmp_df)

res_art_df = pd.concat(res_art_lst)
res_art_df['datetime'] = res_art_df['datetime'].dt.strftime("%Y-%m-%d")

In [27]:
res_art_df

topic                                                url  \
0     Общество/Россия  https://www.rbc.ru/rbcfreenews/67468ac09a7947f...   
1     Общество/Россия  https://www.rbc.ru/society/26/12/2024/676d5bb7...   
2     Общество/Россия  https://www.rbc.ru/rbcfreenews/676a61479a79473...   
3     Общество/Россия  https://www.rbc.ru/rbcfreenews/676437b39a79470...   
4     Общество/Россия  https://www.rbc.ru/rbcfreenews/674dce899a79472...   
...               ...                                                ...   
1638        Экономика  https://www.rbc.ru/economics/20/06/2024/6673f4...   
1639        Экономика  https://www.rbc.ru/economics/17/09/2024/66e965...   
1640        Экономика  https://www.rbc.ru/economics/16/09/2024/66e406...   
1641        Экономика  https://www.rbc.ru/economics/12/09/2024/66e14f...   
1642        Экономика  https://www.rbc.ru/economics/21/12/2023/658302...   

                                                  title  \
0     На Благовещенск обрушилась снежная «буря столе...   
1     Путин подписал закон о новых правилах переселе...   
2     У россиян вырос спрос на туры «все включено» в...   
3     Госдума рассмотрит проект о продлении программ...   
4     Российский турист заявил о снятии с лайнера SH...   
...                                                 ...   
1638  Госдума поддержала поправки о пяти ступенях пр...   
1639  В ЦБ вместо «переохлаждения» экономики допусти...   
1640  Минэк спрогнозировал торможение роста в обраба...   
1641  Минэк заложил в консервативный прогноз «переох...   
1642  Где в России яйца подорожали меньше всего и по...   

                                                content    datetime  
0     Благовещенск в Амурской области накрыла снежна...  2024-11-27  
1     Собственники и наниматели четырехкомнатных и б...  2024-12-26  
2     В 2024 году в России вырос спрос на туры по ст...  2024-12-24  
3     Правительство России внесло в Государственную ...  2024-12-19  
4     Капитан лайнера SH Diana, который прервал круи...  2024-12-02  
...                                                 ...         ...  
1638  Госдума на заседании 20 июня приняла в первом ...  2024-06-20  
1639  Негативный сценарий переохлаждения экономики в...  2024-09-17  
1640  В 2025 году темпы роста промышленного производ...  2024-09-16  
1641  Минэкономразвития разработало консервативный в...  2024-09-12  
1642  Куриные яйца в России продолжают дорожать: за ...  2023-12-21  

[3315 rows x 5 columns]

In [28]:
topic_name_to_lenta_id = {
    'Общество/Россия': 1,
    'Силовые структуры': 37,
    'Бывший СССР': 3,
    'Экономика': 4,
    'Наука и техника': 5,
    'Спорт': 8,
    'Туризм/Путешествия': 48,
    'Здоровье': 87,
    'Строительство': 6
}

res_art_df['topic_id'] = res_art_df['topic'].map(topic_name_to_lenta_id)

In [29]:
res_art_df.to_excel('rbc_econ_and_russia_arts.xlsx')

In [ ]:
res_art_df.to_excel('rbc_arts.xlsx')